In [10]:
%pip install dash
%pip install pyngrok
%pip install plotly
%pip install dash-bootstrap-components

Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.
Note: you may need to restart the kernel to use updated packages.


In [11]:
import dash
import dash.dcc as dcc
import dash.html as html
import plotly.graph_objs as go
from dash.dependencies import Input, Output
import pandas as pd

df = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/WID_Data_12042025-230756.csv", sep=';', engine='python', skiprows=1, header=None)

new_header = ["country", "variable", "percentile", "year", "value"]

df.loc[-1] = new_header            
df.index = df.index + 1            
df = df.sort_index()                

df.columns = df.iloc[0]             
df = df[1:].reset_index(drop=True) 
df['variable'] = 'Top 1%'

df2 = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/WID_Data_12042025-233335.csv", sep=';', engine='python', skiprows=1, header=None)


new_header = ["country", "variable", "percentile", "year", "value"]

df2.loc[-1] = new_header
df2.index = df2.index + 1
df2 = df2.sort_index()

df2.columns = df2.iloc[0]
df2 = df2[1:].reset_index(drop=True)
df2['variable'] = 'Top 10%'

df3 = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/WID_Data_12042025-233501.csv", sep=';', engine='python', skiprows=1, header=None)


new_header = ["country", "variable", "percentile", "year", "value"]

df3.loc[-1] = new_header
df3.index = df3.index + 1
df3 = df3.sort_index()

df3.columns = df3.iloc[0]
df3 = df3[1:].reset_index(drop=True)
df3['variable'] = 'Below 50%'

combined_df = pd.concat([df, df2, df3])
unique_countries = combined_df['country'].unique()

app = dash.Dash(__name__)

app.layout = html.Div([
    html.H1("Country Data Plot for Various Percentiles"),

    dcc.Dropdown(
        id='country-dropdown',
        options=[{'label': country, 'value': country} for country in unique_countries],
        multi=True,
        value=["Afghanistan"],
        placeholder="Select countries",
    ),


    dcc.Dropdown(
        id='percentile-dropdown',
        options=[
            {'label': 'Top 1%', 'value': 'Top 1%'},
            {'label': 'Top 10%', 'value': 'Top 10%'},
            {'label': 'Below 50%', 'value': 'Below 50%'}
        ],
        value='Top 1%',
        placeholder="Select percentile",
    ),

    dcc.Graph(id='line-plot'),
])

@app.callback(
    Output('line-plot', 'figure'),
    [Input('country-dropdown', 'value'),
     Input('percentile-dropdown', 'value')]
)
def update_graph(selected_countries, selected_percentile):
    if selected_percentile == 'Top 1%':
        filtered_df = df[df['variable'] == 'Top 1%']
    elif selected_percentile == 'Top 10%':
        filtered_df = df2[df2['variable'] == 'Top 10%']
    elif selected_percentile == 'Below 50%':
        filtered_df = df3[df3['variable'] == 'Below 50%']

    filtered_df = filtered_df[filtered_df['country'].isin(selected_countries)]

    fig = go.Figure()

    for country in selected_countries:
        country_data = filtered_df[filtered_df['country'] == country]
        fig.add_trace(go.Scatter(
            x=country_data['year'],
            y=country_data['value'],
            mode='lines+markers',
            name=country
        ))

    fig.update_layout(
        title=f"Income Share for {selected_percentile} Percentile",
        xaxis_title="Year",
        yaxis_title="Income Share",
        hovermode="closest"
    )

    return fig

if __name__ == '__main__':
    app.run(debug=True)


In [12]:
import pandas as pd
import plotly.express as px
import numpy as np

def plot_income_share(df, category, selected_df=None):
    if selected_df is None:
        selected_df = df

    year_counts = selected_df['year'].value_counts().sort_index()
    threshold = 100
    valid_years = year_counts[year_counts > threshold]

    if valid_years.empty:
        print(f"Warning: No valid years found for category: {category}. Skipping plot for this category.")
        return

    start_year = valid_years.index[0]
    df_clean = selected_df[selected_df['year'] >= start_year].copy()
    df_clean['year'] = df_clean['year'].astype(int)
    df_clean = df_clean.sort_values(by='year')

    bin_edges = np.arange(0, df_clean['value'].max() + 0.02, 0.02)
    bin_labels = [f"{int(left*100)}–{int(right*100)}%" for left, right in zip(bin_edges[:-1], bin_edges[1:])]
    df_clean['bin'] = pd.cut(df_clean['value'], bins=bin_edges, labels=bin_labels, include_lowest=True)
    df_clean['year'] = df_clean['year'].astype(str)

    color_list = px.colors.qualitative.Safe * 3
    unique_bins = df_clean['bin'].unique().tolist()
    color_map = {label: color_list[i % len(color_list)] for i, label in enumerate(unique_bins)}

    fig = px.choropleth(
        df_clean,
        locations="country",
        locationmode="country names",
        color="bin",
        hover_name="country",
        animation_frame="year",
        color_discrete_map=color_map,
        title=f"{category} Income Share by Country (Distinct 2% Steps)"
    )

    fig.update_layout(
        geo=dict(
            showframe=False,
            showcoastlines=False,
            projection_type="natural earth",
            bgcolor='black'
        ),
        paper_bgcolor='black',
        plot_bgcolor='black',
        font_color='white',
        title_font_size=20,
        legend_title_text="Income Share",
        margin={"r": 0, "t": 50, "l": 0, "b": 0},
        height=600
    )

    fig.show()

def dynamic_category_plot():
    categories = ['Top 1%', 'Top 10%', 'Bottom 50%']
    print("Available categories:")
    for i, category in enumerate(categories, 1):
        print(f"{i}. {category}")

    try:
        choice = int(input(f"Enter the number (1-3) for the category you want to plot: "))
        if choice < 1 or choice > 3:
            raise ValueError("Invalid choice")
    except ValueError as e:
        print(f"Error: {e}")
        return

    selected_category = categories[choice - 1]

    if selected_category == 'Top 1%':
        plot_income_share(df, selected_category)
    elif selected_category == 'Top 10%':
        plot_income_share(df, selected_category, selected_df=df2)
    elif selected_category == 'Bottom 50%':
        plot_income_share(df, selected_category, selected_df=df3)

dynamic_category_plot()


Available categories:
1. Top 1%
2. Top 10%
3. Bottom 50%


In [13]:
import pandas as pd
import dash
from dash import dcc, html
from dash.dependencies import Input, Output
import plotly.express as px

f = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/female_data.csv", sep=';', engine='python', skiprows=1, header=None)

new_header = ["country", "variable", "percentile", "year", "value"]

f.loc[-1] = new_header
f.index = f.index + 1
f = f.sort_index()
f.columns = f.iloc[0]
f = f[1:].reset_index(drop=True)

f["year"] = pd.to_numeric(f["year"], errors='coerce')
f["value"] = pd.to_numeric(f["value"], errors='coerce')

app = dash.Dash(__name__)

app.layout = html.Div([
    html.H1("Female Income Share Over Time"),
    dcc.Dropdown(
        id='country-dropdown',
        options=[{'label': c, 'value': c} for c in sorted(f['country'].unique())],
        value=['Afghanistan'],
        multi=True,
        placeholder="Select countries"
    ),
    dcc.Graph(id='line-plot')
])

@app.callback(
    Output('line-plot', 'figure'),
    [Input('country-dropdown', 'value')]
)
def update_graph(selected_countries):
    if not selected_countries:
        return px.line(title="No countries selected.")

    filtered_df = f[f['country'].isin(selected_countries)]
    fig = px.line(
        filtered_df,
        x='year',
        y='value',
        color='country',
        title='Income Share Over Years',
        markers=True
    )
    fig.update_layout(template='plotly_dark')
    return fig

if __name__ == '__main__':
    app.run(debug=True)


In [14]:
import pandas as pd
import plotly.express as px

gdp = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/GDP_data.csv", sep=';', engine='python', skiprows=1, header=None)

new_header = ["country", "variable", "percentile", "year", "value"]
gdp.loc[-1] = new_header
gdp.index = gdp.index + 1
gdp = gdp.sort_index()
gdp.columns = gdp.iloc[0]
gdp = gdp[1:].reset_index(drop=True)

gdp['year'] = pd.to_numeric(gdp['year'], errors='coerce')
gdp['value'] = pd.to_numeric(gdp['value'], errors='coerce')
gdp = gdp.dropna(subset=['year', 'value'])

gdp['rank'] = gdp.groupby('year')['value'].rank(method='first', ascending=False)
gdp['rank'] = gdp['rank'].astype(int)

gdp = gdp.sort_values(by=['year', 'rank'])

fig = px.scatter(
    gdp,
    x="rank",
    y="value",
    size="value",
    animation_frame="year",
    hover_name="country",
    color="country",
    size_max=60,
    title=" per adult GDP of Country Over Time",
    text="country",
)

fig.update_layout(
    xaxis=dict(title="Rank (1 = Highest GDP)", autorange="reversed"),
    yaxis_title="GDP Value",
    template="plotly_dark",
    height=600,
    showlegend=False,
    margin=dict(t=50, b=40, l=10, r=10),
)

fig.update_traces(textposition="top center")

fig.show()


In [15]:
import pandas as pd
import plotly.express as px

wealth = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/wealth_income.csv", sep=';', engine='python', skiprows=1, header=None)

new_header = ["country", "variable", "percentile", "year", "value"]
wealth.loc[-1] = new_header
wealth.index = wealth.index + 1
wealth = wealth.sort_index()
wealth.columns = wealth.iloc[0]
wealth = wealth[1:].reset_index(drop=True)

wealth['year'] = pd.to_numeric(wealth['year'], errors='coerce')
wealth['value'] = pd.to_numeric(wealth['value'], errors='coerce')
wealth = wealth.dropna(subset=['year', 'value'])

wealth['rank'] = wealth.groupby('year')['value'].rank(method='first', ascending=False).astype(int)

wealth = wealth.sort_values(by=['year', 'rank'])

y_max = wealth['value'].max() * 1.2

fig = px.scatter(
    wealth,
    x="rank",
    y="value",
    size="value",
    animation_frame="year",
    hover_name="country",
    color="country",
    size_max=60,
    title="Wealth/Income ratio Share by Country Over Time",
    text="country"
)

fig.update_layout(
    xaxis=dict(
        title="Rank (1 = Highest Value)",
        autorange="reversed"
    ),
    yaxis=dict(
        title="Wealth/Income Value",
        range=[0, y_max],
    ),
    template="plotly_dark",
    height=600,
    showlegend=False,
    margin=dict(t=50, b=40, l=10, r=10),
)

fig.update_traces(textposition="top center")

fig.show()


In [16]:
import pandas as pd
import plotly.express as px

co2 = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/co2_emmision.csv", sep=';', engine='python', skiprows=1, header=None)

new_header = ["country", "variable", "percentile", "year", "value"]
co2.loc[-1] = new_header
co2.index = co2.index + 1
co2 = co2.sort_index()

co2.columns = co2.iloc[0]
co2 = co2[1:].reset_index(drop=True)

co2['year'] = pd.to_numeric(co2['year'], errors='coerce')
co2['value'] = pd.to_numeric(co2['value'], errors='coerce')
co2 = co2.dropna(subset=['year', 'value'])

fig = px.area(
    co2,
    x="year",
    y="value",
    color="country",
    title=" CO₂ Emissions Area Plot by Country Over Time",
    labels={"value": "CO₂ Emissions", "year": "Year"},
)

fig.update_layout(
    template="plotly_dark",
    height=600,
    margin=dict(t=50, b=40, l=10, r=10),
)

# Show the plot
fig.show()


In [17]:
import pandas as pd
import plotly.express as px

top1 = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/top1_data.csv", sep=';', engine='python', skiprows=1, header=None)
header = ["country", "variable", "percentile", "year", "value"]
top1.loc[-1] = header
top1.index = top1.index + 1
top1 = top1.sort_index()
top1.columns = top1.iloc[0]
top1 = top1[1:].reset_index(drop=True)

top10 = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/top10_data.csv", sep=';', engine='python', skiprows=1, header=None)
top10.loc[-1] = header
top10.index = top10.index + 1
top10 = top10.sort_index()
top10.columns = top10.iloc[0]
top10 = top10[1:].reset_index(drop=True)

bottom50 = pd.read_csv("https://raw.githubusercontent.com/AkashGupta-26/IDS-2025-WritingAssignment/main/data/bottom50_data.csv", sep=';', engine='python', skiprows=1, header=None)
bottom50.loc[-1] = header
bottom50.index = bottom50.index + 1
bottom50 = bottom50.sort_index()
bottom50.columns = bottom50.iloc[0]
bottom50 = bottom50[1:].reset_index(drop=True)

top1['category'] = 'Top 1%'
top10['category'] = 'Top 10%'
bottom50['category'] = 'Bottom 50%'

df = pd.concat([top1, top10, bottom50], ignore_index=True)
df.columns = df.columns.str.strip()
df['year'] = pd.to_numeric(df['year'], errors='coerce')
df['value'] = pd.to_numeric(df['value'], errors='coerce')

df.dropna(subset=['country', 'year', 'category', 'value'], inplace=True)

expected_categories = 3
grouped = df.groupby(['country', 'year'])['category'].nunique().reset_index()
complete_country_years = grouped[grouped['category'] == expected_categories]

df_complete = df.merge(complete_country_years[['country', 'year']], on=['country', 'year'])

countries_per_year = df_complete.groupby('year')['country'].nunique()
total_countries = df_complete['country'].nunique()
valid_years = countries_per_year[countries_per_year == total_countries].index

df_final = df_complete[df_complete['year'].isin(valid_years)]


fig = px.bar(
    df_final,
    x="country",
    y="value",
    color="category",
    animation_frame="year",
    barmode="group",
    title="Wealth Distribution by Country and Category Over Time (Only Complete Years)",
    labels={"value": "Wealth Value", "year": "Year"}
)

fig.update_layout(
    template="plotly_dark",
    height=700,
    margin=dict(t=100, b=200, l=50, r=50),
    legend_title="Category",
    xaxis=dict(
        title="Country",
        tickangle=45,
        tickfont=dict(size=10),
        automargin=True
    ),
    yaxis=dict(
        title="Wealth Value",
        showgrid=True
    ),
    updatemenus=[dict(
        type="buttons",
        direction="left",
        showactive=False,
        x=0.1,
        xanchor="left",
        y=-0.2,
        yanchor="bottom",
        buttons=[
            dict(label="Play", method="animate",
                 args=[None, {"frame": {"duration": 500, "redraw": True}, "fromcurrent": True}]),
            dict(label="Stop", method="animate",
                 args=[[None], {"mode": "immediate", "frame": {"duration": 0, "redraw": True},
                                "transition": {"duration": 0}}])
        ]
    )]
)

fig.update_layout(sliders=[{
    "active": 0,
    "yanchor": "top",
    "xanchor": "left",
    "currentvalue": {
        "font": {"size": 14},
        "prefix": "Year=",
        "visible": True,
        "xanchor": "right"
    },
    "transition": {"duration": 300, "easing": "cubic-in-out"},
    "pad": {"b": 10, "t": 60}
}])

fig.show()


# Income Inequality and Gender Disparity: An Analysis Using the World Inequality Database (WID)

## Introduction

This report analyzes income distribution trends using the World Inequality Database (WID), focusing on income shares of the top 1%, top 10%, and bottom 50% of earners, as well as the share of income earned by women. The dataset spans from 1980 to 2023 and includes data from several regions: the United States, India, Europe, Africa, Asia, and Australia and New Zealand. Visualizations extracted from the dataset aid in interpreting these trends and drawing comparisons across regions.

---

## Summary of the Data

The WID dataset provides critical insights into income inequality through the following categories:

- **Top 1% Income Share**: Measures the share of total income earned by the wealthiest 1%.
- **Top 10% Income Share**: Captures broader elite income accumulation.
- **Bottom 50% Income Share**: Reflects income distribution among the majority of the population.
- **Female Income Share**: Tracks the proportion of national income earned by women.
- **CO₂ Emissions**: Provides context on environmental impacts related to income distribution.
- **GDP per Capita**: Offers insights into economic performance and living standards.
- **Wealth-income Ratios**: Examines the relationship between wealth and income.
  
### Visual Aids

The data has been visualized through time-series plots for each category:

- **Figure 1**: Income Share for the Top 1% Percentile (1980–2023)
  ![alt text](images/Top-1.jpg)

- **Figure 2**: Income Share for the Top 10% Percentile (1980–2023)
  ![alt text](images/Top-10.jpg)

- **Figure 3**: Income Share for the Bottom 50% Percentile (1980–2023)
  ![alt text](images/Below-50.jpg)

- **Figure 4**: Female Income Share Over Years (1990–2023)
  ![alt text](images/Female-Share.jpg)

These visualizations form the basis for hypothesis development and testing.

---

## Hypotheses

Based on the observed data, the following hypotheses are proposed:

1. **Europe has managed income inequality better than the United States since 1980.**
2. **Australia and New Zealand have managed income inequality the best among the regions.**
3. **India’s Top 1% Post-Liberalization Surge and decline of Bottom 50%**
4. **Female Income Share Growth suffers for developing economies**

---

## Methodology for Quantification

To evaluate the hypotheses, we apply the following quantitative measures:

- **Change in Top Share**: The net increase in the top 1% and top 10% income shares over the selected period.
- **Change in Bottom Share**: The net decrease or increase in income share for the bottom 50%.
- **Trend Analysis**: Slope and curvature of lines to assess growth or decline over time.
- **Comparative Gender Metrics**: Relative increases in female income share as a percentage of total income across countries.

These metrics allow us to settle the hypotheses with a data-driven approach.

---

## Analysis and Hypothesis Testing

### Hypothesis 1: Europe vs. United States in Managing Inequality

The top 1% income share in the United States has doubled from approximately 10% in 1980 to 20% in 2020. In contrast, Europe shows a modest increase from around 7% to 10% in the same period. Europe was also able to keep the top 10% income share growth lower than the United States, while matching the wealth-share females had in the society. Data shows that the bottom 50% income share in the United States decreased from approximately 20% in 1980 to 12% in 2020. In Europe, the corresponding decline is smaller and the trend appears more stable.


**Conclusion**: Europe has experienced a slower increase in top income shares, supporting the hypothesis that it has better managed inequality, both in terms of genderwise share and socio-strata. The bottom 50% in the United States has lost a significant portion of income share, while Europe has demonstrated more stability.

---

### Hypothesis 2: Australia and New Zealand have managed income inequality the best among the regions.

Australia and New Zealand show a relatively stable top 1% income share, remaining around 10% from 1980 to 2020. The top 10% income share has also remained stable, with minor fluctuations. The bottom 50% income share has remained relatively constant, indicating a more equitable distribution of income. The portion of income earned by females has also shown a steady increase, reaching around 40% by 2023, highest of all regions.

**Conclusion**: Australia and New Zealand have managed income inequality effectively, with stable top shares and a growing bottom share. The data indicates that these regions have maintained a more equitable income distribution compared to others.

---

### Hypothesis 3: India’s Top 1% Post-Liberalization Surge and decline of Bottom 50%

India's top 1% income share rose from approximately 6% in 1980 to over 22% by 2020. A notable inflection point occurs post-1991, aligning with major economic liberalization policies. Similarly, the top 10% income share has increased significantly, while the bottom 50% share has decreased from around 25% to approximately 15%. The data indicates that the wealthiest have captured a disproportionate share of income growth, while the bottom half has seen a significant decline in their income share. We also observe the stagnation of the female income share at around 15% since 1990, indicating a lack of progress in that direction. 

**Conclusion**: The data clearly demonstrates a significant concentration of income among the top 1% in India following liberalization. The bottom 50% has lost a substantial share of income, indicating rising inequality. The stagnation of female income share further supports the notion that economic growth has not been inclusive.

---

### Hypothesis 4: Female Income Share Growth suffers for developing economies
Europe shows a steady upward trend in female income share, rising from approximately 33% in 1990 to nearly 40% in 2023. Australia and USA show similar trends. In contrast, in regions like Africa, Asia, and India, female income share has stagnated with minimal growth.

**Conclusion**: Gender income equality has improved more in developed economies like Europe and Australia compared to developing regions. The data indicates that while some progress has been made, significant disparities remain, particularly in Asia and Africa.

---

## Discussion

The findings underscore persistent and growing inequalities in certain regions, while also highlighting regions where policy interventions and inclusive economic strategies have mitigated income concentration.

- The United States and India show rising inequality trends, particularly among the highest income percentiles.
- Europe demonstrates relatively stable and inclusive income distribution.
- Gender-based disparities remain deeply entrenched in regions like India, while Europe and Australia show promising progress.

These differences may stem from divergent economic policies, labor regulations, welfare structures, and historical inequalities.

---

## Other Findings
![Emissions](images/CO2.jpg)
### Inference from CO₂ Emissions Area Plot (1980–2019)

The area plot above illustrates CO₂ emissions over time for ten selected countries. A few notable patterns emerge:

1. **United Arab Emirates & United Kingdom Lead in Early Emissions:**
   - In 1980, the United Arab Emirates (UAE) and the United Kingdom (UK) had the highest CO₂ emissions among the selected nations.
   - UAE emissions saw a steep decline during the 1980s and 1990s, stabilizing in the early 2000s with minor fluctuations thereafter.
   - UK emissions exhibited a steady downward trend across the entire timeline, suggesting effective decarbonization policies.

2. **Steady Rise in Emissions from Developing Economies:**
   - India and China display a gradual and sustained rise in emissions starting from the mid-1990s, with China showing a more pronounced increase post-2000. This aligns with their rapid industrial growth during this period.
   - Brazil and Chad show relatively minimal contribution to the overall emissions, remaining nearly constant throughout.

3. **USA and Russia Show Plateauing Trends:**
   - The United States maintains a consistently high level of emissions, although slight reductions are visible post-2005.
   - The Russian Federation’s emissions dip sharply post-1990 (likely due to the Soviet Union’s dissolution), followed by a gradual resurgence and stabilization.

4. **Overall Emissions Composition Shift:**
   - The plot reflects a redistribution of emissions over time, with developed nations like the UK and UAE decreasing their shares while emerging economies such as India and China increase theirs.
   - The total cumulative emissions remain relatively stable from 2000 onward, but with a notable change in country-level contributions.

---

### Inference from Per Adult GDP Bubble Chart (2023)
![GDP per Capita](images/GDP-capita.png)

The bubble chart visualizes per adult GDP of various countries as of 2023, plotted against their GDP rank (where rank 1 corresponds to the highest GDP). The size of each bubble may represent either population or economic size. Key observations include:

1. **USA and UAE Dominate in Per Adult GDP:**
   - The United States stands as the top performer with the highest per adult GDP, indicating a strong economy and high average income.
   - The United Arab Emirates closely follows, showcasing high income per adult likely fueled by oil revenues and a diversified high-income economy.

2. **Significant Gaps Between Developed and Developing Nations:**
   - A clear disparity is visible between developed countries (USA, UAE, UK, Japan) and developing ones (India, Chad, Brazil).
   - Chad occupies the lowest position in both rank and GDP value, highlighting significant economic underdevelopment.
   - India and Brazil show modest GDP per adult, reflecting their emerging economy status.

3. **World Average as Benchmark:**
   - The "World" bubble lies mid-range in both ranking and value, serving as a benchmark to evaluate individual country performance.
   - Countries like China, Brazil, and India fall below the global average, underlining developmental challenges.

4. **Balanced High GDP in European and Asian Nations:**
   - The UK, Japan, and Russia present moderately high GDP per adult, indicating robust yet balanced economies.
   - Japan and the UK closely align with each other, suggesting comparable standards of living.

#### Overall Insight

The chart underscores the stark economic inequality between nations, with a steep gradient from top performers like the USA and UAE down to countries like Chad and India. While emerging economies show gradual improvements, substantial gaps in income distribution remain at a global scale.

---

## Conclusion

This report uses the WID dataset to highlight key global inequality trends across income, environment, and economic development. Income inequality is rising in many liberalized economies, driven by disproportionate gains among top earners. In contrast, regions with strong social policies, like Europe, show slower growth in inequality and better outcomes for lower-income groups.

Gender inequality persists in many developing nations, with progress lagging behind that of Western countries. Visual analyses of CO₂ emissions and GDP per adult further reveal deep global disparities. Developed countries show stabilizing or declining emissions, while emerging economies face rising outputs due to industrialization. Similarly, GDP distribution underscores significant economic gaps between high-income and lower-income countries.

Moving forward, further research should explore underlying causal factors through multivariate analyses and enrich the dataset with additional variables—such as education, healthcare, and urban-rural dynamics—to deepen our understanding of inequality’s causes and consequences.

Ultimately, the WID dataset serves as a robust foundation for assessing the complex interplay of income, environmental sustainability, and social equity.